In [15]:
!wget -O embedder.tflite -q https://storage.googleapis.com/mediapipe-models/image_embedder/mobilenet_v3_small/float32/1/mobilenet_v3_small.tflite


In [1]:
!pip install -q mediapipe==0.10.0
!wget -O embedder.tflite -q https://storage.googleapis.com/mediapipe-models/image_embedder/mobilenet_v3_small/float32/1/mobilenet_v3_small.tflite
!pip install imgaug

zsh:1: command not found: wget
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 948.0/948.0 kB 2.8 MB/s eta 0:00:0000:0100:01
  Obtaining dependency information for scipy from https://files.pythonhosted.org/packages/db/8d/6419a5a65a538791f49d52cd8f8883bd11b41df0c9d35f500c9650f1e0b7/scipy-1.11.1-cp311-cp311-macosx_12_0_arm64.whl.metadata
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 100.3/100.3 kB 1.9 MB/s eta 0:00:00a 0:00:01
  Obtaining dependency information for scikit-image>=0.14.2 from https://files.pythonhosted.org/packages/20/54/06f821fd78c24f7047629dc4c8ed948101fc91fdf660ee3263d870220ae8/scikit_image-0.21.0-cp311-cp311-macosx_12_0_arm64.whl.metadata
  Obtaining dependency information for opencv-python from https://files.pythonhosted.org/packages/b1/ca/69f7f2204d5779ad939123cce9735f76db8f50e2b482e45b413c585b0b27/opencv_python-4.8.0.74-cp37-abi3-macosx_11_0_arm64.whl.metadata
  Obtaining dependency information for imageio from https://files.pythonhosted.org/packages/c7/b0/7b6c35b8636ed

In [1]:
import gdown
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
import mediapipe as mp
from mediapipe.tasks import python
from mediapipe.tasks.python import vision
from tqdm import tqdm
from glob import glob
import gc
import cv2
from PIL import Image
import imgaug as ia
import imgaug.augmenters as iaa
import random
from scipy.spatial.distance import pdist
from csv import DictWriter

In [8]:
url = "https://drive.google.com/file/d/10iRg8rA764Sgm_JScEB6zKalpr8x8xKL/view?usp=share_link"
output = "dataset.zip"
gdown.download(url=url, output=output, quiet=True, fuzzy=True)

'dataset.zip'

In [9]:
!unzip dataset.zip

Archive:  dataset.zip
   creating: content/dataset/
   creating: content/dataset/test/
   creating: content/dataset/test/125/
  inflating: content/dataset/test/125/560661_125_0.jpg  
  inflating: content/dataset/test/125/543734_125_0.jpg  
  inflating: content/dataset/test/125/990919_125_0.jpg  
  inflating: content/dataset/test/125/560349_125_1.jpg  
  inflating: content/dataset/test/125/560750_125_0.jpg  
  inflating: content/dataset/test/125/560349_125_0.jpg  
  inflating: content/dataset/test/125/543804_125_1.jpg  
  inflating: content/dataset/test/125/543804_125_0.jpg  
  inflating: content/dataset/test/125/560349_125_2.jpg  
  inflating: content/dataset/test/125/560661_125_1.jpg  
   creating: content/dataset/test/42/
  inflating: content/dataset/test/42/527153_42_2.jpg  
  inflating: content/dataset/test/42/527109_42_6.jpg  
  inflating: content/dataset/test/42/527273_42_5.jpg  
  inflating: content/dataset/test/42/527225_42_2.jpg  
  inflating: content/dataset/test/42/527153_42

  inflating: content/dataset/test/59/560726_59_4.jpg  
  inflating: content/dataset/test/59/527112_59_1.jpg  
  inflating: content/dataset/test/59/546176_59_2.jpg  
  inflating: content/dataset/test/59/531599_59_3.jpg  
  inflating: content/dataset/test/59/527487_59_3.jpg  
  inflating: content/dataset/test/59/542992_59_1.jpg  
  inflating: content/dataset/test/59/527494_59_1.jpg  
  inflating: content/dataset/test/59/527499_59_1.jpg  
  inflating: content/dataset/test/59/527166_59_6.jpg  
  inflating: content/dataset/test/59/560371_59_0.jpg  
  inflating: content/dataset/test/59/527298_59_1.jpg  
  inflating: content/dataset/test/59/554433_59_0.jpg  
  inflating: content/dataset/test/59/527298_59_2.jpg  
  inflating: content/dataset/test/59/531599_59_5.jpg  
  inflating: content/dataset/test/59/527130_59_0.jpg  
  inflating: content/dataset/test/59/546001_59_1.jpg  
  inflating: content/dataset/test/59/527148_59_2.jpg  
  inflating: content/dataset/test/59/527479_59_2.jpg  
  inflatin

  inflating: content/dataset/test/15/527173_15_1.jpg  
  inflating: content/dataset/test/15/527112_15_1.jpg  
  inflating: content/dataset/test/15/531599_15_0.jpg  
  inflating: content/dataset/test/15/527273_15_0.jpg  
  inflating: content/dataset/test/15/527187_15_4.jpg  
  inflating: content/dataset/test/15/527112_15_7.jpg  
  inflating: content/dataset/test/15/560311_15_6.jpg  
  inflating: content/dataset/test/15/527298_15_1.jpg  
  inflating: content/dataset/test/15/560311_15_4.jpg  
  inflating: content/dataset/test/15/527175_15_5.jpg  
  inflating: content/dataset/test/15/527298_15_0.jpg  
  inflating: content/dataset/test/15/546182_15_0.jpg  
  inflating: content/dataset/test/15/527175_15_4.jpg  
  inflating: content/dataset/test/15/546161_15_0.jpg  
  inflating: content/dataset/test/15/560311_15_2.jpg  
  inflating: content/dataset/test/15/527187_15_6.jpg  
  inflating: content/dataset/test/15/527167_15_0.jpg  
  inflating: content/dataset/test/15/531558_15_1.jpg  
  inflatin

  inflating: content/dataset/test/28/531386_28_0.jpg  
  inflating: content/dataset/test/28/527285_28_2.jpg  
  inflating: content/dataset/test/28/560661_28_4.jpg  
  inflating: content/dataset/test/28/560650_28_1.jpg  
  inflating: content/dataset/test/28/560661_28_2.jpg  
  inflating: content/dataset/test/28/560611_28_1.jpg  
  inflating: content/dataset/test/28/543685_28_1.jpg  
  inflating: content/dataset/test/28/554281_28_0.jpg  
  inflating: content/dataset/test/28/542845_28_9.jpg  
  inflating: content/dataset/test/28/531125_28_3.jpg  
  inflating: content/dataset/test/28/527285_28_1.jpg  
  inflating: content/dataset/test/28/542845_28_14.jpg  
  inflating: content/dataset/test/28/531220_28_2.jpg  
  inflating: content/dataset/test/28/527173_28_1.jpg  
  inflating: content/dataset/test/28/548590_28_3.jpg  
  inflating: content/dataset/test/28/531386_28_5.jpg  
  inflating: content/dataset/test/28/531602_28_3.jpg  
  inflating: content/dataset/test/28/548590_28_0.jpg  
  inflati

  inflating: content/dataset/test/34/527176_34_0.jpg  
  inflating: content/dataset/test/34/527176_34_3.jpg  
  inflating: content/dataset/test/34/560121_34_2.jpg  
  inflating: content/dataset/test/34/926333_34_2.jpg  
  inflating: content/dataset/test/34/531578_34_3.jpg  
  inflating: content/dataset/test/34/527492_34_0.jpg  
  inflating: content/dataset/test/34/546131_34_2.jpg  
  inflating: content/dataset/test/34/527176_34_2.jpg  
  inflating: content/dataset/test/34/527206_34_3.jpg  
  inflating: content/dataset/test/34/527285_34_4.jpg  
  inflating: content/dataset/test/34/548691_34_6.jpg  
  inflating: content/dataset/test/34/527494_34_0.jpg  
  inflating: content/dataset/test/34/546017_34_2.jpg  
  inflating: content/dataset/test/34/546131_34_1.jpg  
  inflating: content/dataset/test/34/527219_34_0.jpg  
  inflating: content/dataset/test/34/926338_34_0.jpg  
  inflating: content/dataset/test/34/527130_34_1.jpg  
  inflating: content/dataset/test/34/531578_34_1.jpg  
  inflatin

...

  inflating: dataset/test/531041_130_1.jpg  
  inflating: dataset/test/527173_7_1.jpg  
  inflating: dataset/test/527499_54_0.jpg  
  inflating: dataset/test/554433_153_0.jpg  
  inflating: dataset/test/548709_6_0.jpg  
  inflating: dataset/test/560524_65_1.jpg  
  inflating: dataset/test/531492_9_0.jpg  
  inflating: dataset/test/990277_99_0.jpg  
  inflating: dataset/test/926118_55_2.jpg  
  inflating: dataset/test/531586_88_7.jpg  
  inflating: dataset/test/560579_28_0.jpg  
  inflating: dataset/test/527150_5_2.jpg  
  inflating: dataset/test/527115_75_2.jpg  
  inflating: dataset/test/527277_9_1.jpg  
  inflating: dataset/test/926100_8_1.jpg  
  inflating: dataset/test/527109_67_2.jpg  
  inflating: dataset/test/527503_5_11.jpg  
  inflating: dataset/test/925968_1_1.jpg  
  inflating: dataset/test/548690_59_0.jpg  
  inflating: dataset/test/527160_6_11.jpg  
  inflating: dataset/test/527220_66_2.jpg  
  inflating: dataset/test/546004_52_1.jpg  
  inflating: dataset/test/554384_28_0

  inflating: dataset/test/527206_40_6.jpg  
  inflating: dataset/test/560520_53_0.jpg  
  inflating: dataset/test/925882_137_0.jpg  
  inflating: dataset/test/560778_3_0.jpg  
  inflating: dataset/test/527488_39_0.jpg  
  inflating: dataset/test/527501_41_1.jpg  
  inflating: dataset/test/527512_23_1.jpg  
  inflating: dataset/test/554447_2_1.jpg  
  inflating: dataset/test/527100_25_5.jpg  
  inflating: dataset/test/542998_60_0.jpg  
  inflating: dataset/test/926320_5_4.jpg  
  inflating: dataset/test/531589_104_8.jpg  
  inflating: dataset/test/531489_33_43.jpg  
  inflating: dataset/test/926267_138_4.jpg  
  inflating: dataset/test/531250_73_1.jpg  
  inflating: dataset/test/560891_7_1.jpg  
  inflating: dataset/test/548685_51_0.jpg  
  inflating: dataset/test/926275_66_6.jpg  
  inflating: dataset/test/527220_81_2.jpg  
  inflating: dataset/test/925900_107_0.jpg  
  inflating: dataset/test/554317_36_0.jpg  
  inflating: dataset/test/926014_55_0.jpg  
  inflating: dataset/test/53148

  inflating: dataset/test/531267_100_11.jpg  
  inflating: dataset/test/546000_10_0.jpg  
  inflating: dataset/test/560559_66_2.jpg  
  inflating: dataset/test/527213_65_23.jpg  
  inflating: dataset/test/527482_101_1.jpg  
  inflating: dataset/test/527205_6_2.jpg  
  inflating: dataset/test/531578_6_19.jpg  
  inflating: dataset/test/926287_83_2.jpg  
  inflating: dataset/test/527299_41_1.jpg  
  inflating: dataset/test/554429_71_0.jpg  
  inflating: dataset/test/925882_24_1.jpg  
  inflating: dataset/test/560608_5_7.jpg  
  inflating: dataset/test/527176_2_3.jpg  
  inflating: dataset/test/531579_33_1.jpg  
  inflating: dataset/test/546002_10_0.jpg  
  inflating: dataset/test/527169_41_1.jpg  
  inflating: dataset/test/527193_21_0.jpg  
  inflating: dataset/test/543704_5_0.jpg  
  inflating: dataset/test/527139_6_0.jpg  
  inflating: dataset/test/545535_69_1.jpg  
  inflating: dataset/test/531603_8_0.jpg  
  inflating: dataset/test/531574_107_0.jpg  
  inflating: dataset/test/531573_

  inflating: dataset/test/531599_62_0.jpg  
  inflating: dataset/test/527302_2_3.jpg  
  inflating: dataset/test/548684_92_0.jpg  
  inflating: dataset/test/546005_20_7.jpg  
  inflating: dataset/test/548694_68_1.jpg  
  inflating: dataset/test/527297_37_6.jpg  
  inflating: dataset/test/560665_62_0.jpg  
  inflating: dataset/test/531588_114_0.jpg  
  inflating: dataset/test/531605_2_9.jpg  
  inflating: dataset/test/554392_38_0.jpg  
  inflating: dataset/test/531142_69_3.jpg  
  inflating: dataset/test/531573_54_2.jpg  
  inflating: dataset/test/560640_98_0.jpg  
  inflating: dataset/test/542998_137_8.jpg  
  inflating: dataset/test/548724_135_1.jpg  
  inflating: dataset/test/531521_50_0.jpg  
  inflating: dataset/test/926320_1_3.jpg  
  inflating: dataset/test/531580_5_1.jpg  
  inflating: dataset/test/527277_10_6.jpg  
  inflating: dataset/test/531573_33_12.jpg  
  inflating: dataset/test/543789_73_1.jpg  
  inflating: dataset/test/527501_24_4.jpg  
  inflating: dataset/test/531382

  inflating: dataset/test/542991_76_14.jpg  
  inflating: dataset/test/531494_81_1.jpg  
  inflating: dataset/test/554374_11_0.jpg  
  inflating: dataset/test/527101_57_0.jpg  
  inflating: dataset/test/546095_37_0.jpg  
  inflating: dataset/test/926369_5_3.jpg  
  inflating: dataset/test/527277_15_5.jpg  
  inflating: dataset/test/554446_41_2.jpg  
  inflating: dataset/test/926282_57_6.jpg  
  inflating: dataset/test/527188_86_0.jpg  
  inflating: dataset/test/554409_78_3.jpg  
  inflating: dataset/test/560327_95_2.jpg  
  inflating: dataset/test/531578_34_3.jpg  
  inflating: dataset/test/530924_76_2.jpg  
  inflating: dataset/test/545549_24_0.jpg  
  inflating: dataset/test/527485_24_8.jpg  
  inflating: dataset/test/546007_21_1.jpg  
  inflating: dataset/test/554444_135_2.jpg  
  inflating: dataset/test/546164_137_0.jpg  
  inflating: dataset/test/548708_146_0.jpg  
  inflating: dataset/test/531602_43_24.jpg  
  inflating: dataset/test/926115_60_0.jpg  
  inflating: dataset/test/52

In [2]:
def prepare_mobile_net_embeddings(source_path):
    # Create options for Image Embedder
    base_options = python.BaseOptions(model_asset_path='embedder.tflite')
    l2_normalize = True
    quantize = False
    options = vision.ImageEmbedderOptions(
      base_options=base_options, l2_normalize=l2_normalize, quantize=quantize)

    images = []
    labels = {}
    with vision.ImageEmbedder.create_from_options(options) as embedder:
        for image in tqdm(glob(f'{source_path}/*.jpg', recursive=True)):
            image_sample = {}
            splitted_path = image.split("/")[-1]
            image_sample["Id"] = splitted_path
            image_sample["label"] = splitted_path.split("_")[1]
            
            first_image = mp.Image.create_from_file(image)
                    # Format images for MediaPipe
            first_embedding_result = embedder.embed(first_image)

            
            emb = first_embedding_result.embeddings[0].embedding.tolist()
            for i  in range(len(emb)):
                image_sample[f"embedding_{i}"] = emb[i]
            images.append(image_sample)
    return images

In [3]:
def get_n_train(X_train, y_train, n):
    y_res = pd.Series()
    X_res = pd.DataFrame()
    for ind in y_train.unique():
        try:
            y_sample = y_train[y_train == ind].sample(n=n)
        except:
            y_sample = y_train[y_train == ind].sample(n=len(y_train[y_train == ind]))
        X_sample = X_train.loc[y_sample.index]
        y_res = pd.concat([y_res,y_sample])
        X_res = pd.concat([X_res,X_sample])
    return X_res, y_res

In [4]:
train_data = prepare_mobile_net_embeddings("dataset/train")
train_df= pd.DataFrame(train_data)
#test_df.to_csv("test.csv")

INFO: Created TensorFlow Lite XNNPACK delegate for CPU.
100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 40458/40458 [02:17<00:00, 294.42it/s]


In [7]:
X_train = train_df.loc[:, 'embedding_0':'embedding_1023']
y_train = train_df["label"]
cutted_X, cutted_y = get_n_train(X_train, y_train, 100)
test = pd.read_csv("test.csv")
X_test = test.loc[:, 'embedding_0':'embedding_1023']
y_test = test["label"]

In [15]:
cutted_y

5449      22
22457     22
9116      22
14512     22
9828      22
        ... 
21354    127
16039    127
21782    109
18730    109
24637     91
Length: 1541, dtype: object

In [8]:
params_1 = {'n_neighbors': 4, 'weights': 'distance', 'leaf_size': 72, 'metric': 'cosine'}
clf = KNeighborsClassifier(**params_1)
clf.fit(cutted_X, cutted_y)
clf.score(X_test, y_test)

0.0

In [28]:
def prepare_mobile_net_embeddings_aug_save_scv(image_pathes, seq, filename = "train.csv",
                                               aug_number = 30, buffer_size = 10000):
    # Create options for Image Embedder
    base_options = python.BaseOptions(model_asset_path='embedder.tflite')
    l2_normalize = True
    quantize = False
    options = vision.ImageEmbedderOptions(
      base_options=base_options, l2_normalize=l2_normalize, quantize=quantize)
    
    field_names = ['Id', 'label']
    for i in range(1024):
        field_names.append(f"embedding_{i}")

    with open(filename, 'a') as f_object:
        dictwriter_object = DictWriter(f_object, fieldnames=field_names)
        dictwriter_object.writeheader()
        
    images = []
    tmp = 0
    with vision.ImageEmbedder.create_from_options(options) as embedder:
        for image in tqdm(image_pathes):
            image_sample = {}
            splitted_path = image.split("/")[-1]
            image_sample["Id"] = splitted_path.split(".")[0]
            image_sample["label"] = splitted_path.split("_")[1]
            
            tmp += 1
            
            im = load_image(image).squeeze()
            images_np = np.array(
            [im for _ in range(aug_number)],
            dtype=np.uint8
            )
            images_aug = seq(images=images_np)
            
            emb = np.zeros(1024,)
            for img in images_aug:
                img_for_mp = mp.Image(image_format=mp.ImageFormat.SRGB, data=img)
                #with vision.ImageEmbedder.create_from_options(options) as embedder:
                    #first_image = mp.Image.create_from_file(image)
                    # Format images for MediaPipe
                first_embedding_result = embedder.embed(img_for_mp)
                emb = first_embedding_result.embeddings[0].embedding
                emb = emb.tolist()
                for i  in range(len(emb)):
                    image_sample[f"embedding_{i}"] = emb[i]
                images.append(image_sample)
            
            if tmp >= buffer_size:
                with open(filename, 'a') as f_object:
                    dictwriter_object = DictWriter(f_object, fieldnames=field_names)
                    dictwriter_object.writerows(images)
                images = []
                tmp = 0
                gc.collect

    with open(filename, 'a') as f_object:
        dictwriter_object = DictWriter(f_object, fieldnames=field_names)
        dictwriter_object.writerows(images)

    return images

In [ ]:
image_pathes = glob("dataset/train/*.jpg")
seq = get_augmentator(params)
prepare_mobile_net_embeddings_aug_save_scv(image_pathes, seq, filename = "train.csv",
                                               aug_number = 30, buffer_size = 1000)

 97%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍     | 39080/40458 [1:04:57<01:56, 11.88it/s]

In [29]:
def load_image( infilename ) :
    img = Image.open( infilename )
    img.load()
    data = np.asarray( img, dtype="uint8" )
    return data

def save_image( npdata, outfilename ) :
    img = Image.fromarray( npdata )
    img.save( outfilename )
    
def prepare_mobile_net_embeddings_aug_for_label(image_pathes, seq, label, aug_number = 8, sample_length = 500):
    # Create options for Image Embedder
    base_options = python.BaseOptions(model_asset_path='embedder.tflite')
    l2_normalize = True
    quantize = False
    options = vision.ImageEmbedderOptions(
      base_options=base_options, l2_normalize=l2_normalize, quantize=quantize)

    images = []
    tmp = 0
    with vision.ImageEmbedder.create_from_options(options) as embedder:
        for image in image_pathes:
            image_sample = {}
            splitted_path = image.split("/")[-1]
            image_sample["Id"] = splitted_path.split(".")[0]
            image_sample["label"] = splitted_path.split("_")[1]
            if image_sample["label"] == str(label):
                tmp += 1
                im = load_image(image).squeeze()
                images_np = np.array(
                [im for _ in range(aug_number)],
                dtype=np.uint8
                )
                images_aug = seq(images=images_np)
                emb = np.zeros(1024,)
                for img in images_aug:
                    img_for_mp = mp.Image(image_format=mp.ImageFormat.SRGB, data=img)
                    #with vision.ImageEmbedder.create_from_options(options) as embedder:
                        #first_image = mp.Image.create_from_file(image)
                        # Format images for MediaPipe
                    first_embedding_result = embedder.embed(img_for_mp)
                    emb = first_embedding_result.embeddings[0].embedding
                    emb = emb.tolist()
                    for i  in range(len(emb)):
                        image_sample[f"embedding_{i}"] = emb[i]
                    images.append(image_sample)
            if tmp >= sample_length:
                print("Done")
                break
    return images

In [30]:
def prepare_mobile_net_embeddings_for_label(image_pathes, label):
    # Create options for Image Embedder
    base_options = python.BaseOptions(model_asset_path='embedder.tflite')
    l2_normalize = True
    quantize = False
    options = vision.ImageEmbedderOptions(
      base_options=base_options, l2_normalize=l2_normalize, quantize=quantize)

    images = []
    with vision.ImageEmbedder.create_from_options(options) as embedder:
        for image in tqdm(image_pathes):
            image_sample = {}
            splitted_path = image.split("/")[-1]
            image_sample["Id"] = splitted_path.split(".")[0]
            image_sample["label"] = splitted_path.split("_")[1]
            if image_sample["label"] == str(label):
                first_image = mp.Image.create_from_file(image)
                        # Format images for MediaPipe
                first_embedding_result = embedder.embed(first_image)

                emb = first_embedding_result.embeddings[0].embedding.tolist()
                for i  in range(len(emb)):
                    image_sample[f"embedding_{i}"] = emb[i]
                images.append(image_sample)
    return images

In [31]:
params = {'horiz_flip_prob': 0.23372002393841368,
          'vert_flip_prob': 0.003580711334931301,
          'crop_prob': 0.020424702330632562,
          'crop_max_value': 0.2552338768996226,
          'affine_scale_x': 0.32408282439318215,
          'affine_scale_y': 0.02278775623930282,
          'affine_translate_x': 0.7341285974850827,
          'affine_translate_y': 0.20893062419459313,
          'affine_rotate': 45,
          'affine_shear': 87,
          'affine_mode': ["symmetric"],
          'max_number_of_strong_aug': 0,
          'gausian_blur_sigma': 0.22334345487784962,
          'average_blur_kernel': 4.742900261926021,
          'motion_blur_kernel': 9,
          'motion_blur_angle': 26,
          'piecewise_affine_scale': 0.031810750909470616}

In [32]:
def get_augmentator(params):
    sometimes = lambda aug: iaa.Sometimes(params["crop_prob"], aug)

    seq = iaa.Sequential(
        [
            #
            # Apply the following augmenters to most images.
            #
            iaa.Fliplr(params["horiz_flip_prob"]), # horizontally flip 30% of all images
            iaa.Flipud(params["vert_flip_prob"]), # vertically flip 10% of all images

            # crop some of the images by 0-10% of their height/width
            sometimes(iaa.Crop(percent=(0, params["crop_max_value"]))),

            # Apply affine transformations to some of the images
            # - scale to 80-120% of image height/width (each axis independently)
            # - translate by -20 to +20 relative to height/width (per axis)
            # - rotate by -45 to +45 degrees
            # - shear by -16 to +16 degrees
            # - order: use nearest neighbour or bilinear interpolation (fast)
            # - mode: use any available mode to fill newly created pixels
            #         see API or scikit-image for which modes are available
            # - cval: if the mode is constant, then use a random brightness
            #         for the newly created pixels (e.g. sometimes black,
            #         sometimes white)
            sometimes(iaa.Affine(
                scale={"x": (1 - params["affine_scale_x"], 1 + params["affine_scale_x"]),
                       "y": (1 - params["affine_scale_y"], 1 + params["affine_scale_y"])},
                translate_percent={"x": (-params["affine_translate_x"], params["affine_translate_x"]),
                                   "y": (-params["affine_translate_y"], params["affine_translate_y"])},
                rotate=(-params["affine_rotate"], params["affine_rotate"]),
                shear=(-params["affine_shear"], params["affine_shear"]),
                order=[0, 1],
                cval=(0, 255),
                mode=params["affine_mode"]
            )),

            #
            # Execute 0 to 5 of the following (less important) augmenters per
            # image. Don't execute all of them, as that would often be way too
            # strong.
            #
            iaa.SomeOf((0, params["max_number_of_strong_aug"]),
                [

                    # Blur each image with varying strength using
                    # gaussian blur (sigma between 0 and 3.0),
                    # average/uniform blur (kernel size between 2x2 and 7x7)
                    # median blur (kernel size between 3x3 and 11x11).
                    iaa.OneOf([
                        iaa.GaussianBlur(params["gausian_blur_sigma"]),
                        iaa.AverageBlur(k=params["average_blur_kernel"]),
                    ]),


                    # Add gaussian noise to some images.
                    # In 50% of these cases, the noise is randomly sampled per
                    # channel and pixel.
                    # In the other 50% of all cases it is sampled once per
                    # pixel (i.e. brightness change).
                    iaa.AdditiveGaussianNoise(
                        loc=0, scale=(0.0, 0.05*255)
                    ),

                    iaa.MotionBlur(k=params["motion_blur_kernel"], angle=[-params["motion_blur_angle"],
                                                                       params["motion_blur_angle"]]),

                    # Change brightness of images (50-150% of original value).
                    iaa.Multiply((0.8, 1.3), per_channel=0.5),

                    # In some images distort local areas with varying strength.
                    sometimes(iaa.PiecewiseAffine(scale=(params["piecewise_affine_scale"])))
                ],
                # do all of the above augmentations in random order
                random_order=True
            )
        ],
        # do all of the above augmentations in random order
        random_order=True
    )
    return seq

In [33]:
def AndrewFunction(dataset_path, params, label=0, sample_length=500, aug_number=3):
    image_pathes = glob(f"{dataset_path}/*.jpg")
    random.shuffle(image_pathes)
    seq = get_augmentator(params)
    aug_data = prepare_mobile_net_embeddings_aug_for_label(image_pathes, seq,
                                                           label, aug_number = aug_number,
                                                           sample_length = sample_length)
    random.shuffle(image_pathes)
    data = prepare_mobile_net_embeddings_for_label(image_pathes, label)
    df = pd.DataFrame(data)
    aug_df = pd.DataFrame(aug_data)
    features = df.loc[:, 'embedding_0':'embedding_1023']
    aug_features = aug_df.loc[:, 'embedding_0':'embedding_1023']
    distances = pdist(features, metric="cosine")
    aug_distances = pdist(aug_features, metric="cosine")
    return distances, aug_distances

In [34]:
def CoolAndrewFunction(dataset_path, params, labels=[0, 1], sample_length=500, aug_number=3):
    image_pathes = glob(f"{dataset_path}/*.jpg")
    random.shuffle(image_pathes)
    seq = get_augmentator(params)
    y_res = pd.Series()
    X_res = pd.DataFrame()
    for label in tqdm(labels):
        aug_data = prepare_mobile_net_embeddings_aug_for_label(image_pathes, seq,
                                                              label, aug_number = aug_number,
                                                              sample_length = sample_length)
        aug_df = pd.DataFrame(aug_data)
        aug_features = aug_df.loc[:, 'embedding_0':'embedding_1023']
        aug_labels = aug_df["label"]
        y_res = pd.concat([y_res, aug_labels])
        X_res = pd.concat([X_res, aug_features])
    return X_res, y_res

In [40]:
def get_scores(X_test, y_test, labels, params):
    scores = {key:0 for key in [2**i for i in range(11)]}
    params_1 = {'n_neighbors': 4, 'weights': 'distance', 'leaf_size': 72, 'metric': 'cosine'}
    for n in tqdm(scores.keys()):
        X_train_temp, y_train_temp = CoolAndrewFunction("dataset/train", params, labels=labels, sample_length=n, aug_number=20)
        clf = KNeighborsClassifier(**params_1)
        clf.fit(X_train_temp, y_train_temp)
        scores[n] = clf.score(X_test, y_test)
        print(scores[n])
    return scores

In [41]:
def CoolResultAndrewFunction(X_test, y_test, labels, params, aug_number, sample_length, support = 1400):
    while aug_number * sample_length >= support:
        sample_length -= 1
    
    params_1 = {'n_neighbors': 4, 'weights': 'distance', 'leaf_size': 72, 'metric': 'cosine'}

    X_train_temp, y_train_temp = CoolAndrewFunction("dataset/train", params, labels=labels, sample_length=sample_length, aug_number=aug_number)
    clf = KNeighborsClassifier(**params_1)
    clf.fit(X_train_temp, y_train_temp)
    score = clf.score(X_test, y_test)

    return score

In [37]:
X_test = test_df.loc[:, 'embedding_0':'embedding_1023']
y_test = test_df["label"]
labels = y_test.unique()

In [38]:
np.bool = np.bool_

In [14]:
len(labels)

155

In [43]:
CoolResultAndrewFunction(X_test, y_test, labels, params, aug_number=100, sample_length=10, support=10000)

  1%|█                                                                                                                                                                          | 1/155 [00:02<07:29,  2.92s/it]

Done


  1%|██▏                                                                                                                                                                        | 2/155 [00:05<07:20,  2.88s/it]

Done


  2%|███▎                                                                                                                                                                       | 3/155 [00:08<07:12,  2.85s/it]

...

Done


 99%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊  | 153/155 [07:52<00:07,  3.51s/it]

Done


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 155/155 [07:59<00:00,  3.09s/it]


0.43997864551555826